In [165]:
# %%
import pandas as pd
import numpy as np
import time
import plotly.graph_objects as go

from neuralforecast import NeuralForecast
from neuralforecast.models import NBEATS, NHITS, TFT
from neuralforecast.auto import AutoMLP, AutoDeepAR, AutoNBEATS, AutoNHITS, AutoTFT, AutoDeepNPTS

from statsforecast.core import StatsForecast
from statsforecast.models import (
    Naive,
    SeasonalNaive,
    ARIMA,
    SimpleExponentialSmoothing,
    SimpleExponentialSmoothingOptimized,
    SeasonalExponentialSmoothing,
    SeasonalExponentialSmoothingOptimized,
    RandomWalkWithDrift,
    ETS,
    HistoricAverage,
    WindowAverage,
    AutoARIMA,
    AutoETS,
    AutoCES,
    AutoTheta
)

from mlforecast import MLForecast
from xgboost import XGBRegressor
from catboost import CatBoostRegressor
from sklearn.ensemble import RandomForestRegressor
import lightgbm as lgb

from mlforecast.target_transforms import Differences
from mlforecast.lag_transforms import ExpandingMean, RollingMean
from numba import njit
from window_ops.rolling import rolling_mean

from ray import tune
from nixtla import NixtlaClient

import warnings
warnings.filterwarnings("ignore")

In [166]:

# %%
def evaluate_forecast(y_true, y_pred):
    return np.sqrt(np.mean((y_true.values - y_pred.values) ** 2))

def smape(y_true, y_pred):
    return 100 * np.mean(np.abs(y_pred - y_true) / (np.abs(y_true) + np.abs(y_pred)) / 2)

def rmsse(y_true, y_pred, train):
    naive_forecast = np.roll(train, 1)
    naive_forecast[0] = train[0]
    scale = np.mean((train - naive_forecast) ** 2)
    return np.sqrt(np.mean((y_true - y_pred) ** 2) / scale)

def calculate_errors(test, forecasts, train):
    df = pd.DataFrame()
    for col in forecasts.columns:
        if col in ['ds', 'unique_id']:
            continue
        y_true = test['y'].values
        y_pred = forecasts[col].values
        error_dict = {
            'RMSE': evaluate_forecast(test['y'], forecasts[col]),
            'SMAPE': smape(y_true, y_pred),
            'RMSSE': rmsse(y_true, y_pred, train['y'].values)
        }
        df = pd.concat([pd.DataFrame(error_dict, index=[col]), df])
    return df

# %%
# Load the AirPassengers dataset
from statsforecast.utils import AirPassengersDF
df = AirPassengersDF
forecast_horizons = [24, 3, 6, 12]
test_size_total = 24
train_size_total = len(df) - test_size_total
train_total, test_total = df[:train_size_total], df[train_size_total:]

df.to_csv('Air_passengers.csv')


In [167]:

# %%
@njit
def rolling_mean_12(x):
    return rolling_mean(x, window_size=12)

def month_index(times):
    return times.month


In [168]:

# %%
# Model definitions
statistical_models = [
    Naive(),
    SeasonalNaive(12),
    ARIMA(order=[12, 1, 0]),
    ARIMA(order=[0, 1, 1], seasonal_order=[0, 1, 1], season_length=12, alias='SARIMA'),
    SimpleExponentialSmoothing(alpha=0.28),
    ETS(model='AAA', season_length=12, alias='ETS AAA'),
    ETS(model='MAM', season_length=12, alias='ETS MAM'),
    ETS(model='MMM', season_length=12, alias='ETS MMM'),
    ETS(model='MMM', season_length=12, alias='ETS MMdM', damped=True),
    ETS(model='MAM', season_length=12, alias='ETS MAdM', damped=True),
    HistoricAverage(),
    WindowAverage(window_size=6),
    AutoARIMA(max_p=12),
    AutoETS(season_length=12),
    AutoETS(season_length=12, damped=True, alias='Damped AutoETS'),
    AutoCES(season_length=12, alias='AutoCES'),
    AutoTheta(season_length=12),
    SimpleExponentialSmoothingOptimized(),
    SeasonalExponentialSmoothing(season_length=12, alpha=0.28),
    SeasonalExponentialSmoothingOptimized(season_length=12),
    RandomWalkWithDrift()
]

lgb_params = {'verbosity': -1, 'num_leaves': 512}
catboost_params = {'subsample': 0.6, 'iterations': 50, 'depth': 5, 'verbose': 0}
xgboost_params = {'verbosity': 0, 'max_depth': 5, 'subsample': 0.6}
randomforest_params = {'verbose': 0, 'max_depth': 5}

tree_models = [
    [{'LightGBM': lgb.LGBMRegressor(**lgb_params)}],
    [{'CatBoost': CatBoostRegressor(**catboost_params)}],
    [{'XgBoost': XGBRegressor(**xgboost_params)}],
    [{'RandomForest': RandomForestRegressor(**randomforest_params)}],
]

neural_models_template = [
    NBEATS(input_size=2 * test_size_total, h=test_size_total,max_steps=20),
    NHITS(input_size=2 * test_size_total, h=test_size_total,max_steps=20),
    AutoMLP(config=dict(input_size=tune.choice([3 * test_size_total]),max_steps=20, learning_rate=tune.choice([1e-3])), h=test_size_total, num_samples=1, cpus=3, verbose=False),
    # AutoDeepAR(config=dict(input_size=tune.choice([3 * test_size_total]), learning_rate=tune.choice([1e-3])), h=test_size_total, num_samples=1, cpus=3),
    # AutoNBEATS(config=dict(input_size=tune.choice([3 * test_size_total]), learning_rate=tune.choice([1e-3])), h=test_size_total, num_samples=1, cpus=3),
    # AutoNHITS(config=dict(input_size=tune.choice([3 * test_size_total]), learning_rate=tune.choice([1e-3])), h=test_size_total, num_samples=1, cpus=3),
    # AutoTFT(config=dict(input_size=tune.choice([3 * test_size_total]), learning_rate=tune.choice([1e-3])), h=test_size_total, num_samples=1, cpus=3)
]

from nixtla import NixtlaClient
nixtla_client = NixtlaClient(
    api_key = 'nixtla-tok-BWWtvgUP9FLtzerA90xyzXPvRUoZvA0OYYp5cuSI7NZUyApQjlINlF8dAyYXqDyxWlTlCOg7jXHWJV4o'
)


Seed set to 1
Seed set to 1


In [169]:
def forecast_and_evaluate(models, model_type, forecast_horizons, train_total, test_total, df):
    error_dfs = []
    forecasts_by_horizon = {horizon: [] for horizon in forecast_horizons}
    
    for model in models:
        for horizon in forecast_horizons:
            total_train_time = 0
            combined_forecasts = pd.DataFrame()

            for start in range(0, test_size_total, horizon):
                train_size = train_size_total + start
                train = df[:train_size]
                test = df[train_size:train_size + horizon]

                if model_type == 'statistical':
                    sf = StatsForecast(models=[model], freq='M', n_jobs=-1)
                    start_time = time.time()
                    forecasts_df = sf.forecast(df=train, h=horizon)
                    
                elif model_type == 'tree':
                    fcst = MLForecast(
                        models=model[0],
                        freq="M",
                        target_transforms=[Differences([12])],
                        lags=[1, 2, 3, 4, 11, 12],
                        lag_transforms={1: [ExpandingMean()], 12: [RollingMean(window_size=12), rolling_mean_12]},
                        date_features=[month_index]
                    )
                    model_tree = model[0].keys()
                    start_time = time.time()
                    fcst.fit(train)
                    forecasts_df = fcst.predict(h=horizon)
                    
                elif model_type == 'neural':
                    nf = NeuralForecast(models=[model], freq='M')
                    start_time = time.time()
                    nf.fit(df=train)
                    forecasts_df = nf.predict().reset_index()[:horizon]
                    
                elif model_type == 'TimeGPT':
                    start_time = time.time()
                    forecasts_df = nixtla_client.forecast(df=train, h=horizon, freq='M', time_col='ds', target_col='y')
                    
                train_time = time.time() - start_time
                forecasts_df['origin'] = train_size  # Track the forecast origin point
                combined_forecasts = pd.concat([combined_forecasts, forecasts_df])
                total_train_time += train_time

            # Calculate errors for the combined forecast
            combined_error = calculate_errors(test_total, combined_forecasts.drop(columns=['origin']), train_total)
            combined_error['Total_Train_Time'] = total_train_time
            combined_error['Horizon'] = horizon
            combined_error['Model'] = str(model)
            if model_type == 'tree':
                combined_error['Model'] = model_tree
            error_dfs.append(combined_error)
            forecasts_by_horizon[horizon].append(combined_forecasts)
    
    return pd.concat(error_dfs).reset_index(drop=True), forecasts_by_horizon

In [170]:
# Forecast and evaluate tree-based models
tree_errors, tree_forecasts_by_horizon  = forecast_and_evaluate(tree_models, 'tree', forecast_horizons, train_total, test_total, df)

In [171]:
# Forecast and evaluate statistical models
statistical_errors, statistical_forecasts_by_horizon  = forecast_and_evaluate(statistical_models, 'statistical', forecast_horizons, train_total, test_total, df)

In [172]:

TimeGPT_errors, TimeGPT_forecasts_by_horizon = forecast_and_evaluate(['TimeGPT'], 'TimeGPT', forecast_horizons, train_total, test_total, df)

INFO:nixtla.nixtla_client:Validating inputs...
INFO:nixtla.nixtla_client:Preprocessing dataframes...
INFO:nixtla.nixtla_client:Inferred freq: ME
INFO:nixtla.nixtla_client:Restricting input...
INFO:nixtla.nixtla_client:Calling Forecast Endpoint...
INFO:nixtla.nixtla_client:Validating inputs...
INFO:nixtla.nixtla_client:Preprocessing dataframes...
INFO:nixtla.nixtla_client:Inferred freq: ME
INFO:nixtla.nixtla_client:Restricting input...
INFO:nixtla.nixtla_client:Calling Forecast Endpoint...
INFO:nixtla.nixtla_client:Validating inputs...
INFO:nixtla.nixtla_client:Preprocessing dataframes...
INFO:nixtla.nixtla_client:Inferred freq: ME
INFO:nixtla.nixtla_client:Restricting input...
INFO:nixtla.nixtla_client:Calling Forecast Endpoint...
INFO:nixtla.nixtla_client:Validating inputs...
INFO:nixtla.nixtla_client:Preprocessing dataframes...
INFO:nixtla.nixtla_client:Inferred freq: ME
INFO:nixtla.nixtla_client:Restricting input...
INFO:nixtla.nixtla_client:Calling Forecast Endpoint...
INFO:nixtla.

In [182]:
# Forecast and evaluate neural models
neural_errors, neural_forecasts_by_horizon = forecast_and_evaluate(neural_models_template, 'neural', forecast_horizons, train_total, test_total, df)

(_train_tune pid=24556) c:\Users\91976\Desktop\Forecast_llm_comparison\.env\lib\site-packages\ray\tune\integration\pytorch_lightning.py:198: `ray.tune.integration.pytorch_lightning.TuneReportCallback` is deprecated. Use `ray.tune.integration.pytorch_lightning.TuneReportCheckpointCallback` instead.
(_train_tune pid=24556) Seed set to 1
(_train_tune pid=24556) c:\Users\91976\Desktop\Forecast_llm_comparison\.env\lib\site-packages\neuralforecast\common\_base_model.py:208: UserWarning: val_check_steps is greater than max_steps, setting val_check_steps to max_steps.
(_train_tune pid=24556)   warnings.warn(
(_train_tune pid=24556) GPU available: False, used: False
(_train_tune pid=24556) TPU available: False, using: 0 TPU cores
(_train_tune pid=24556) IPU available: False, using: 0 IPUs
(_train_tune pid=24556) HPU available: False, using: 0 HPUs
(_train_tune pid=24556) Missing logger folder: C:\Users\91976\AppData\Local\Temp\ray\session_2024-07-09_03-58-36_708415_22616\artifacts\2024-07-09_04

Epoch 17:   0%|          | 0/1 [00:00<?, ?it/s, v_num=0, train_loss_step=46.70, train_loss_epoch=46.70]        


2024-07-09 04:02:44,232	WARNING experiment_state.py:205 -- Experiment state snapshotting has been triggered multiple times in the last 5.0 seconds. A snapshot is forced if `CheckpointConfig(num_to_keep)` is set, and a trial has checkpointed >= `num_to_keep` times since the last snapshot.
You may want to consider increasing the `CheckpointConfig(num_to_keep)` or decreasing the frequency of saving checkpoints.
You can suppress this error by setting the environment variable TUNE_WARN_EXCESSIVE_EXPERIMENT_CHECKPOINT_SYNC_THRESHOLD_S to a smaller value than the current threshold (5.0).
2024-07-09 04:02:44,232	INFO tune.py:1007 -- Wrote the latest version of all result files and experiment state to 'C:/Users/91976/ray_results/_train_tune_2024-07-09_04-02-31' in 0.0166s.
Seed set to 1
(_train_tune pid=24556) `Trainer.fit` stopped: `max_steps=20` reached.
GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 

Epoch 19: 100%|██████████| 1/1 [00:00<00:00, 12.08it/s, v_num=0, train_loss_step=45.10, train_loss_epoch=52.00]
Validation: |          | 0/? [00:00<?, ?it/s]
Epoch 19: 100%|██████████| 1/1 [00:00<00:00, 10.00it/s, v_num=0, train_loss_step=45.10, train_loss_epoch=45.10, valid_loss=56.60]



  | Name         | Type          | Params
-----------------------------------------------
0 | loss         | MAE           | 0     
1 | padder_train | ConstantPad1d | 0     
2 | scaler       | TemporalNorm  | 0     
3 | mlp          | ModuleList    | 1.1 M 
4 | out          | Linear        | 24.6 K
-----------------------------------------------
1.1 M     Trainable params
0         Non-trainable params
1.1 M     Total params
4.596     Total estimated model params size (MB)


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

`Trainer.fit` stopped: `max_steps=20` reached.
GPU available: False, used: False
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

In [183]:
import os

output_dir = 'forecasts_by_horizon'
os.makedirs(output_dir, exist_ok=True)

def save_forecasts_by_horizon(forecasts_by_horizon, model_type):
    for horizon, forecasts_list in forecasts_by_horizon.items():
        combined_forecasts = pd.concat(forecasts_list).reset_index(drop=True)
        combined_forecasts.to_csv(os.path.join(output_dir, f'{model_type}_forecasts_horizon_{horizon}.csv'), index=False)

save_forecasts_by_horizon(statistical_forecasts_by_horizon, 'statistical')
save_forecasts_by_horizon(tree_forecasts_by_horizon, 'tree')
save_forecasts_by_horizon(TimeGPT_forecasts_by_horizon, 'TimeGPT')
# save_forecasts_by_horizon(neural_forecasts_by_horizon, 'neural')

In [184]:
import plotly.graph_objects as go

def plot_all_forecasts(df, forecasts_by_horizon):
    fig = go.Figure()

    # Add actual data
    fig.add_trace(go.Scatter(x=df['ds'], y=df['y'], mode='lines', name='Actual'))

    # Add forecasts
    for horizon, forecasts_list in forecasts_by_horizon.items():
        combined_forecasts = pd.concat(forecasts_list).reset_index(drop=True)
        for col in combined_forecasts.columns:
            if col in ['ds', 'unique_id', 'origin']:
                continue
            fig.add_trace(go.Scatter(x=combined_forecasts['ds'], y=combined_forecasts[col], mode='lines', name=f'{col} (Horizon {horizon})'))

    fig.update_layout(title='All Forecasts by Horizon', xaxis_title='Date', yaxis_title='Passengers')
    fig.show()


In [185]:

plot_all_forecasts(df, {**statistical_forecasts_by_horizon})

In [186]:
plot_all_forecasts(df, { **tree_forecasts_by_horizon,})


In [187]:
plot_all_forecasts(df, {**TimeGPT_forecasts_by_horizon})


In [188]:
# %%
# Plot all forecasts combined
import plotly.graph_objects as go

def plot_all_forecasts(df, forecasts_by_horizon, model_type):
    fig = go.Figure()

    # Add actual data
    fig.add_trace(go.Scatter(x=df['ds'], y=df['y'], mode='lines', name='Actual'))

    # Add forecasts
    for horizon, forecasts_list in forecasts_by_horizon.items():
        combined_forecasts = pd.concat(forecasts_list).reset_index(drop=True)
        for col in combined_forecasts.columns:
            if col in ['ds', 'unique_id', 'origin']:
                continue
            fig.add_trace(go.Scatter(x=combined_forecasts['ds'], y=combined_forecasts[col], mode='lines', name=f'{col} (Horizon {horizon})'))

    fig.update_layout(title=f'All Forecasts by Horizon ({model_type})', xaxis_title='Date', yaxis_title='Passengers')
    fig.show()

# Plot forecasts for statistical models
plot_all_forecasts(df, statistical_forecasts_by_horizon, 'statistical')

# Plot forecasts for tree-based models
plot_all_forecasts(df, tree_forecasts_by_horizon, 'tree')

# Plot forecasts for neural models
# plot_all_forecasts(df, neural_forecasts_by_horizon, 'neural')

# Plot forecasts for TimeGPT
plot_all_forecasts(df, TimeGPT_forecasts_by_horizon, 'TimeGPT')

# %%
# Plot forecasts separately by horizon
def plot_forecasts_by_horizon(df, forecasts_by_horizon, model_type):
    for horizon, forecasts_list in forecasts_by_horizon.items():
        fig = go.Figure()

        # Add actual data
        fig.add_trace(go.Scatter(x=df['ds'], y=df['y'], mode='lines', name='Actual'))

        # Add forecasts for the current horizon
        combined_forecasts = pd.concat(forecasts_list).reset_index(drop=True)
        for col in combined_forecasts.columns:
            if col in ['ds', 'unique_id', 'origin']:
                continue
            fig.add_trace(go.Scatter(x=combined_forecasts['ds'], y=combined_forecasts[col], mode='lines', name=f'{col} (Horizon {horizon})'))

        fig.update_layout(title=f'Forecasts for Horizon {horizon} ({model_type})', xaxis_title='Date', yaxis_title='Passengers')
        fig.show()

# Plot forecasts for statistical models by horizon
plot_forecasts_by_horizon(df, statistical_forecasts_by_horizon, 'statistical')

# Plot forecasts for tree-based models by horizon
plot_forecasts_by_horizon(df, tree_forecasts_by_horizon, 'tree')

# Plot forecasts for neural models by horizon
# plot_forecasts_by_horizon(df, neural_forecasts_by_horizon, 'neural')

# Plot forecasts for TimeGPT by horizon
plot_forecasts_by_horizon(df, TimeGPT_forecasts_by_horizon, 'TimeGPT')


In [189]:
import plotly.express as px
import plotly.graph_objects as go

all_errors = pd.concat([statistical_errors, tree_errors, TimeGPT_errors])

# %%
# Find and display the minimum errors sorted list per horizon
min_errors_by_horizon = all_errors.groupby('Horizon').apply(lambda x: x.nsmallest(1, 'RMSSE')).reset_index(drop=True)
min_errors_by_horizon = min_errors_by_horizon.sort_values(by=['Horizon', 'RMSSE'])


train_times = all_errors.groupby('Model')['Total_Train_Time'].mean().sort_values().reset_index()


def plot_min_errors_by_horizon(min_errors_by_horizon):
    min_errors_by_horizon['Horizon'] = min_errors_by_horizon['Horizon'].astype('str')
    fig = px.bar(min_errors_by_horizon, 
                 x='Horizon', 
                 y='RMSSE', 
                 color='Model',
                 title='Minimum RMSSE by Horizon',
                 labels={'Horizon': 'Horizon', 'RMSE': 'RMSSE', 'Model': 'Model'},
                 barmode='group'
                )
    fig.update_layout(
        xaxis_title='Horizon',
        yaxis_title='RMSSE',
        legend_title='Model',
        xaxis = dict(
            tickmode = 'linear',
            tick0 = 0,
            dtick = 1
        )
    )
    fig.show()

plot_min_errors_by_horizon(min_errors_by_horizon)


def plot_horizon_metrics(metrics):
    metrics['Horizon'] = metrics['Horizon'].astype('str')
    fig = px.bar(metrics, x='Horizon', y='RMSE', color='Model', barmode='group', title='RMSE by Horizon')
    fig.update_layout(
        xaxis_title="Horizon",
        yaxis_title="RMSE",
        showlegend=True
    )
    fig.show()
    
plot_horizon_metrics(all_errors)

# Correlation between Training Time and Error Metrics
def correlation_train_time_errors(errors):
    metrics = [ 'RMSSE']
    for metric in metrics:
        fig = px.scatter(errors, x='Total_Train_Time', y=metric, color='Model', title=f'Correlation between Training Time and {metric}')
        fig.update_layout(yaxis_title=metric, xaxis_title='Total Train Time (seconds)')
        fig.show()

correlation_train_time_errors(all_errors)

# Training Time Comparison by Model Type
def train_time_comparison_by_type(errors):
    train_times = errors.groupby('Model')['Total_Train_Time'].mean().sort_values().reset_index()
    fig = px.bar(train_times, x='Model', y='Total_Train_Time', title='Average Training Time by Model Type')
    fig.update_layout(yaxis_title='Training Time (seconds)', xaxis_title='Model Type')
    fig.show()

train_time_comparison_by_type(all_errors)

# Best Performing Models by Horizon and Model Type
def best_models_by_horizon_and_type(errors):
    best_models = errors.groupby(['Horizon', 'Model']).mean().reset_index()
    best_models = best_models.sort_values(by=['Horizon', 'RMSE'])
    fig = px.line(best_models, x='Horizon', y='RMSE', color='Model', title='Best Performing Models by Horizon and Model Type')
    fig.update_layout(yaxis_title='RMSE', xaxis_title='Horizon')
    fig.show()

best_models_by_horizon_and_type(all_errors)

# Performance Stability over Different Horizons
def performance_stability(errors):
    stability = errors.groupby('Model').std().reset_index()
    stability = stability.sort_values(by='RMSE')
    fig = px.bar(stability, x='Model', y='RMSE', title='Performance Stability (Standard Deviation of RMSE) over Different Horizons')
    fig.update_layout(yaxis_title='Standard Deviation of RMSE', xaxis_title='Model')
    fig.show()

performance_stability(all_errors)

# Summarize Insights
def summarize_insights(min_errors_by_horizon, train_times):
    print("Minimum Errors Sorted List per Horizon")
    print(min_errors_by_horizon)

    print("\nAverage Training Time by Model")
    print(train_times)


# summarize_insights(min_errors_by_horizon, train_times)


In [190]:
import plotly.express as px

# Aggregate RMSSE across all models and horizons
overall_rmsse = all_errors.groupby('Model')['RMSSE'].mean().reset_index()
overall_rmsse = overall_rmsse.sort_values(by='RMSSE')

# Plotting the best overall model
fig = px.bar(overall_rmsse, x='Model', y='RMSSE', title='Overall RMSSE by Model')
fig.update_layout(yaxis_title='RMSSE', xaxis_title='Model')
fig.show()